In [1]:
%load_ext autoreload
%autoreload 2

In [29]:

import json
import json
import logging

from pgvector.psycopg import register_vector
import psycopg
import numpy as np
import pandas as pd
from shapely.geometry import Polygon
import geopandas as gpd
import pyproj
pyproj.datadir.set_data_dir('/Users/jm/Code/mapgpt-mvp/.conda/share/proj')
import matplotlib.pyplot as plt
import os
import sys
from dotenv import load_dotenv
import pandas as pd
import pydeck as pdk
from IPython.display import display
sys.path.append('../src')

from infrastructure.gpt4 import GPT4
from infrastructure.postgres_db import PostgresDB
from application.maps.choropleth_map import ChoroplethMap
import plotly.graph_objects as go
from infrastructure.gpt4 import generate_openai_embedding_request

load_dotenv()
gpt4 = GPT4()

db_name = os.environ.get("DB_NAME")
db_user = os.environ.get("DB_USER")
db_password = os.environ.get("DB_PASSWORD")


db = PostgresDB(db_name=db_name, db_user=db_user, db_password=db_password)
comunas = db.run_gpd_query("SELECT * FROM comuna")

# Function to extract coordinates
def get_polygon_coordinates(geom):
    if geom.type == 'Polygon':
        return [(x, y) for x, y in geom.exterior.coords]
    elif geom.type == 'MultiPolygon':
        return [[(x, y) for x, y in polygon.exterior.coords] for polygon in geom.geoms][0]
    else:
        return None

comunas = comunas.to_crs(epsg=4326)
np.random.seed(9)
comunas = comunas.assign(
    lat = comunas.geom.centroid.y,
    lon = comunas.geom.centroid.x,
    coordinates = comunas.geom.apply(lambda geom: [list(coord) for coord in geom.geoms[0].exterior.coords]),
    coordinates2 = comunas.geom.apply(get_polygon_coordinates),
    score=lambda _df: np.random.randint(0, 101, size=len(_df)),
    score1=lambda _df: np.random.randint(0, 101, size=len(_df)),
    score2=lambda _df: np.random.randint(0, 101, size=len(_df)),
    score3=lambda _df: np.random.randint(0, 101, size=len(_df)),
    # geom = comunas.geom.simplify(10, preserve_topology=True)


    
)
# comunas.geom = comunas.geom.simplify(10, preserve_topology=True)
comunas = comunas.to_crs(epsg=3857)
c = comunas.set_index("codigo").head(10)
c.geom = c.geom.simplify(10, preserve_topology=True)
d = comunas.set_index("codigo").tail(10)
d.geom = d.geom.simplify(10, preserve_topology=True)


/Users/jm/Code/mapgpt-mvp/.conda/lib/python3.11/site-packages/geopandas/io/sql.py:185: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(
/Users/jm/Code/mapgpt-mvp/.conda/lib/python3.11/site-packages/geopandas/io/sql.py:473: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  return pd.read_sql(spatial_ref_sys_sql, con)
/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykernel_26523/238503318.py:47: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  lat = comunas.geom.centroid.y,
/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykerne

In [24]:
df1 = db.run_gpd_query("""
SELECT c.nombre AS candidato,
       m.nombre AS mesa,
       vm.votos AS votos,
       geom
FROM votos_mesa AS vm
JOIN mesa AS m ON vm.mesa_id = m.id
JOIN candidatura AS ca ON vm.candidatura_id = ca.id
JOIN candidato AS c ON ca.candidato_id = c.id
JOIN eleccion AS e ON ca.eleccion_id = e.id
JOIN comuna AS co ON m.comuna_id = co.id
WHERE co.nombre = 'Paredones'
  AND e.nombre = 'Presidencial 2021 Primera Vuelta'
  AND c.nombre = 'Gabriel Boric Font'
""")

/Users/jm/Code/mapgpt-mvp/.conda/lib/python3.11/site-packages/geopandas/io/sql.py:185: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(


In [46]:
import folium


# cm = ChoroplethMap(df1, "votos")



# Convert GeoDataFrame to GeoJSON
geojson = df1.to_geo_dict()

# Create a folium map object
fig = folium.Map(width=500, height=500)

choropleth = folium.Choropleth(
    geo_data=df1.head(1),
    name="candidato",
    data=df1.head(1),
    columns=[df1.head(1).index, "votos"],
    key_on="feature.id",
    fill_color="viridis",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="aa",
).add_to(fig)

folium.GeoJsonTooltip(['candidato', 'votos']).add_to(choropleth.geojson)

folium.LayerControl().add_to(fig)

fig.fit_bounds(fig.get_bounds())

display(fig)

In [26]:
df1.explore()

In [20]:
# query = f"""SELECT nombre 
#        FROM candidatos 
#        ORDER BY {order_by} <=> '{embedding_str}' LIMIT 1;"""

emb_openai_small


1536

NameError: name 'emb_openai_small' is not defined

In [17]:
print()

SELECT *
FROM candidatos
WHERE nombre = 'Jorge Sharp'


In [ ]:
gpt4.send_batch_embedding()

# Candidatos

In [3]:
nombres = pd.read_sql("SELECT DISTINCT nombre FROM candidato", con=db.engine)["nombre"]

# Generate embeddings

In [4]:
requests = [generate_openai_embedding_request(i, text) for i, text in enumerate(nombres)]

# batch_id = gpt4.send_batch_embedding(requests, "batch_embedding__candidato_nombre.jsonl")

In [42]:
import tiktoken
enc = tiktoken.get_encoding("o200k_base")
assert enc.decode(enc.encode("hello world")) == "hello world"

# To get the tokeniser corresponding to a specific model in the OpenAI API:
enc = tiktoken.encoding_for_model("gpt-4o")
nombres.dropna().apply(enc.encode).apply(len).sum() * 1e-8

In [8]:
# db.get_most_similar_levenstein("candidato", "nombre", "gabriel boric")

column = "nombre"
table = "candidato"
pd.read_sql(f"""SELECT {column} 
            FROM {table} 
            ORDER BY levenshtein({column}, %s) 
            LIMIT 1;""", con=db.engine, params=("gabriel boricc",))[column].iloc[0]

'Gabriel Boric Font'

In [58]:
gpt4.get_batch("batch_AjTQEw9RRt4KpmwTOpAVgqtt").output_file_id

'file-FhsaTfA6J0Zzd1LSk5l4LPOM'

In [6]:
content = gpt4.client.files.content(gpt4.get_batch("batch_AjTQEw9RRt4KpmwTOpAVgqtt").output_file_id)
# content.write_to_file(output_path)
content

In [61]:


content_dicts = list(map(json.loads, content.iter_lines()))
requests_df = pd.DataFrame([{"custom_id": d["custom_id"], "input": d["body"]["input"]} for d in requests]).set_index("custom_id")
responses_df = pd.DataFrame([{"custom_id": d["custom_id"], "embedding": d["response"]["body"]["data"][0]["embedding"]} for d in content_dicts]).set_index("custom_id")
name_embedding = requests_df.join(responses_df).set_index("input")["embedding"].dropna().to_dict()

In [ ]:
# content = self.client.files.content(output_file_id)
# content.write_to_file(output_path)

In [ ]:
gpt4.get_batch_result(batch_AjTQEw9RRt4KpmwTOpAVgqtt, "batch_embedding__candidato_nombre_result.jsonl")

# Save embeddings

In [62]:

import tqdm


db.create_connection()
suffix = "emb_openai_small"
table = "candidato"
column = "nombre"
# embedding_column = f"{column}__{suffix}"

with db.conn.cursor() as cur:
    cur.execute('CREATE EXTENSION IF NOT EXISTS vector')
    
register_vector(db.conn)

with db.conn.cursor() as cur:
    with cur.copy(f"COPY embeddings_openai_small (table_name, column_name, text, embedding) FROM STDIN WITH (FORMAT BINARY)") as copy:
            for name, embedding in tqdm.tqdm(name_embedding.items(), total=len(name_embedding)):
                # formatted_embedding = [round(num, 6) for num in embedding]
                embedding_str = json.dumps(embedding, separators=(',', ':'))
                copy.set_types(["text", "text", "text", "vector"])
                copy.write_row([table, column, name, embedding])
    db.conn.commit()
   

100%|██████████| 41104/41104 [00:18<00:00, 2219.69it/s]


In [58]:
xx = pd.DataFrame(name_embedding.items(), columns=["nombre", "embedding"])
xx

nombre  \
0              Juan Fidel Troncoso Sandoval   
1                    Agustina Salazar Rozas   
2                     Gonzalo Cataldo Tello   
3      Jessica Del Carmen Oyanedel Oyanedel   
4            Freddy Luis Fuentealba Sanzana   
...                                     ...   
41100           Alexis Rodrigo Wood Escobar   
41101     Nancy Eugenia Valenzuela Sanhueza   
41102       Francisco Javier Briceño Zuñiga   
41103               Marisol Turres Figueroa   
41104          Carlos Antonio Videla Castro   

                                               embedding  
0      [0.048109643, -0.021553453, -0.00040810078, -0...  
1      [-0.010063605, 0.043627977, -0.009251921, 0.03...  
2      [-0.01443282, -0.033310626, 0.020792363, 0.003...  
3      [0.06258098, -0.015779829, -0.0002653103, 0.03...  
4      [0.015517292, -0.054429114, -0.008083222, -0.0...  
...                                                  ...  
41100  [0.029894726, 0.014036679, -0.007819741, 0.001...  
41101  [0.032429058, -0.01682005, -0.030477932, -0.00...  
41102  [-0.0120496135, 0.020387314, 0.0015019708, -0....  
41103  [0.029288407, -0.014500044, -0.0009137611, 0.0...  
41104  [0.04209977, -0.007538588, -0.023085527, -0.03...  

[41105 rows x 2 columns]

In [60]:
xx.embedding.dropna().apply(len)

0        1536
1        1536
2        1536
3        1536
4        1536
         ... 
41100    1536
41101    1536
41102    1536
41103    1536
41104    1536
Name: embedding, Length: 41104, dtype: int64

In [43]:
len(name_embedding.items())

41105

In [42]:
db.conn.commit()

In [38]:
table, clembedding_column

('candidato', 'nombre__emb_openai_small')

In [27]:
pip install "psycopg[binary,pool]"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 15.1 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 197.7/197.7 kB 18.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [18]:
embedding_str = json.dumps(formatted_embedding, separators=(',', ':'))
embedding_str

'[0.04811,-0.021553,-0.000408,-0.002074,-0.005883,-0.009834,0.026848,0.065286,-0.002169,-0.057115,-0.019875,0.01702,-0.011131,-0.011527,-0.02172,-0.013612,-0.053363,-0.02887,0.000167,-0.016822,-0.001337,0.0185,0.003903,-0.029829,-0.01677,0.022179,-0.023721,0.004349,-0.021011,-0.004732,0.038354,-0.023784,-0.009953,-0.027265,0.010058,0.005524,0.040314,-0.02147,0.023158,0.004646,0.01135,-0.04344,0.024993,0.015613,0.053321,-0.007483,-0.035811,0.01136,0.004964,0.003192,-0.010151,0.011412,0.017906,0.070622,-0.013049,-0.012757,-0.034727,-0.055197,0.002864,-0.032726,-0.030829,-0.015852,-0.007968,0.04048,-0.001083,0.006801,0.016978,0.008724,0.004234,0.020657,-0.037062,0.03283,0.002457,0.01776,0.041231,0.031767,0.039084,-0.017041,-0.037375,-0.052654,-0.010725,0.017666,0.009755,-0.001558,-0.030162,0.019886,-0.027327,0.044441,0.031517,0.003463,-0.027578,0.012288,-0.018343,0.00238,0.000132,-0.020584,0.047401,-0.022012,0.048527,-0.021845,0.005461,0.015863,0.018468,-0.036499,0.000141,0.03381,0.065578

In [9]:
from application.services.sql_utils import to_geospatial_query
from sqlparse import format

query = """
SELECT v.votos, c.nombre AS candidato_nombre, m.nombre 
AS mesa_nombre, cm.nombre AS comuna_nombre, 
e.nombre AS eleccion_nombre, e.fecha AS eleccion_fecha 
FROM votos_mesa AS v JOIN candidatura AS cd 
ON v.candidatura_id = cd.id JOIN candidato AS c 
ON cd.candidato_id = c.id JOIN mesa AS m ON v.mesa_id = m.id 
JOIN comuna AS cm ON m.comuna_id = cm.id 
JOIN eleccion AS e ON cd.eleccion_id = e.id 
WHERE c.nombre = 'Gabriel Boric Font' 
AND e.nombre = 'Presidencial 2021 Primera Vuelta' 
AND cm.nombre = 'Paredones'
"""

# to_geospatial_query(query, {"comuna": "geom"})

formatted_query = format(to_geospatial_query(query, {"comuna": "geom"}), reindent=True, keyword_case='upper')
print(formatted_query)

SELECT v.votos,
       c.nombre AS candidato_nombre,
       m.nombre AS mesa_nombre,
       cm.nombre AS comuna_nombre,
       e.nombre AS eleccion_nombre,
       e.fecha AS eleccion_fecha,
       geom
FROM votos_mesa AS v
JOIN candidatura AS cd ON v.candidatura_id = cd.id
JOIN candidato AS c ON cd.candidato_id = c.id
JOIN mesa AS m ON v.mesa_id = m.id
JOIN comuna AS cm ON m.comuna_id = cm.id
JOIN eleccion AS e ON cd.eleccion_id = e.id
WHERE c.nombre = 'Gabriel Boric Font'
  AND e.nombre = 'Presidencial 2021 Primera Vuelta'
  AND cm.nombre = 'Paredones'


In [7]:
from bidict import bidict
from sqlglot import parse_one, exp


parsed_query = parse_one(query)
table_alias = bidict({t.alias:t.name for t in parsed_query.find_all(exp.Table)})
table_names = [t.name for t in parsed_query.find_all(exp.Table)]
geospatial_columns =  {"comuna": "geom"}
if parsed_query is None:
    raise ValueError(f"Query {query} could not be parsed.")

for col in geospatial_columns:
    if col not in table_names:
        raise ValueError(f"Geotable {col} not found in query.")


select = parsed_query.find(exp.Select)
group_by = parsed_query.find(exp.Group)

if select is None:
    raise ValueError(f"Query {query} does not contain a SELECT clause.")

# if select contains comuna, add geom
geospatial_exp = [e for e in select.expressions if type(e) == exp.Column and table_alias[e.table] in geospatial_columns.keys()]
geospatial_exp

[]

In [ ]:
data  = db.run_gpd_query()

In [21]:
print(db.get_schema())

CREATE TABLE votos_mesa (
  id integer NOT NULL,
  mesa_id integer,
  candidatura_id integer,
  votos integer
);
CREATE TABLE mesa (
  id integer NOT NULL,
  comuna_id integer,
  nombre text,
  nombre_local text,
  nombre_circunscripcion_electoral text
);
CREATE TABLE eleccion (
  id integer NOT NULL,
  tipo_eleccion_id integer,
  fecha date,
  nombre text
);
CREATE TABLE pacto (
  id integer NOT NULL,
  nombre text,
  codigo text
);
CREATE TABLE partido (
  id integer NOT NULL,
  nombre text
);
CREATE TABLE region (
  id integer NOT NULL,
  codigo integer,
  nombre text
);
CREATE TABLE subpacto (
  id integer NOT NULL,
  nombre text
);
CREATE TABLE tipo_eleccion (
  id integer NOT NULL,
  nombre text
);
CREATE TABLE candidatura (
  id integer NOT NULL,
  candidato_id integer,
  eleccion_id integer,
  partido_id integer,
  pacto_id integer,
  subpacto_id integer,
  num_en_papeleta integer,
  independiente boolean
);
CREATE TABLE candidato (
  id integer NOT NULL,
  nombre__emb_openai_s

In [ ]:
cm = ChoroplethMap()